Datos originales

In [19]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import mean_absolute_error
import numpy as np

# Cargar los datos
train_features = pd.read_csv("dengue_features_train.csv")
train_labels = pd.read_csv("dengue_labels_train.csv")

# Unir las etiquetas con las características para análisis más sencillo
data = train_features.merge(train_labels, on=["city", "year", "weekofyear"])

# Separar por ciudad
data_sj = data[data["city"] == "sj"].drop(columns=["city"])
data_iq = data[data["city"] == "iq"].drop(columns=["city"])

# Características (sin la fecha y etiquetas)
features = [col for col in data_sj.columns if col not in ["total_cases", "week_start_date"]]

# Función para evaluar los modelos
def evaluate_advanced_models(data, selected_features, imputer, scaler, transformation="log"):
    X = data[selected_features]
    y = data["total_cases"]

    # Separar en entrenamiento y prueba
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Imputación
    X_train = imputer.fit_transform(X_train)
    X_test = imputer.transform(X_test)

    # Aplicar transformación logarítmica
    if transformation == "log":
        X_train = np.log1p(np.abs(X_train))  # log(1 + x) para evitar problemas con ceros
        X_test = np.log1p(np.abs(X_test))

    # Escalado
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Modelos
    models = {
        "RandomForest": RandomForestRegressor(n_estimators=100, random_state=42),
        "XGBoost": XGBRegressor(n_estimators=100, random_state=42),
        "LightGBM": LGBMRegressor(n_estimators=100, random_state=42),
        "KNN": KNeighborsRegressor(n_neighbors=5),
        "NaiveBayes": GaussianNB()
    }

    results = {}
    for name, model in models.items():
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        results[name] = mean_absolute_error(y_test, y_pred)

    return results

# Imputador y escalador
imputer_sj = SimpleImputer(strategy="most_frequent")
imputer_iq = SimpleImputer(strategy="median")
scaler = StandardScaler()

# Evaluar para San Juan e Iquitos
results_sj = evaluate_advanced_models(data_sj, features, imputer_sj, scaler, "log")
results_iq = evaluate_advanced_models(data_iq, features, imputer_iq, scaler, "log")

# Crear DataFrame con los resultados
df_results = pd.DataFrame([results_sj, results_iq], index=["San Juan", "Iquitos"])

# Mostrar la tabla en el notebook
display(df_results.style.set_caption("Resultados de Modelos DengAI"))


c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000405 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3816
[LightGBM] [Info] Number of data points in the train set: 748, number of used features: 22
[LightGBM] [Info] Start training from score 34.330214
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


Datos clean

In [21]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import mean_absolute_error
import numpy as np
from IPython.display import display

# Cargar los datos LIMPIOS
data_sj = pd.read_csv("analisis/train_sj_clean.csv")
data_iq = pd.read_csv("analisis/train_iq_clean.csv")

# Características (sin la fecha y etiquetas)
features_sj = [col for col in data_sj.columns if col not in ["total_cases", "week_start_date"]]
features_iq = [col for col in data_iq.columns if col not in ["total_cases", "week_start_date"]]

# Función para evaluar los modelos
def evaluate_advanced_models(data, selected_features, imputer, scaler, transformation="log"):
    X = data[selected_features]
    y = data["total_cases"]

    # Separar en entrenamiento y prueba
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Imputación
    X_train = imputer.fit_transform(X_train)
    X_test = imputer.transform(X_test)

    # Aplicar transformación logarítmica
    if transformation == "log":
        X_train = np.log1p(np.abs(X_train))  # log(1 + x) para evitar problemas con ceros
        X_test = np.log1p(np.abs(X_test))

    # Escalado
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Modelos
    models = {
        "RandomForest": RandomForestRegressor(n_estimators=100, random_state=42),
        "XGBoost": XGBRegressor(n_estimators=100, random_state=42),
        "LightGBM": LGBMRegressor(n_estimators=100, random_state=42),
        "KNN": KNeighborsRegressor(n_neighbors=5),
        "NaiveBayes": GaussianNB()
    }

    results = {}
    for name, model in models.items():
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        results[name] = mean_absolute_error(y_test, y_pred)

    return results

# Imputador y escalador
imputer_sj = SimpleImputer(strategy="most_frequent")
imputer_iq = SimpleImputer(strategy="median")
scaler = StandardScaler()

# Evaluar para San Juan e Iquitos usando los datos LIMPIOS
results_sj = evaluate_advanced_models(data_sj, features_sj, imputer_sj, scaler, "log")
results_iq = evaluate_advanced_models(data_iq, features_iq, imputer_iq, scaler, "log")

# Crear DataFrame con los resultados
df_results = pd.DataFrame([results_sj, results_iq], index=["San Juan", "Iquitos"])

# Mostrar la tabla en el notebook
display(df_results)


c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000159 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3839
[LightGBM] [Info] Number of data points in the train set: 748, number of used features: 22
[LightGBM] [Info] Start training from score 34.330214
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


RandomForest    XGBoost   LightGBM        KNN  NaiveBayes
San Juan     15.322181  12.136500  16.724204  23.800000    32.62766
Iquitos       5.751442   5.510869   5.644914   7.344231     9.50000

Clean 2

In [23]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import mean_absolute_error
import numpy as np
from IPython.display import display

# Cargar los datos LIMPIOS
data_sj = pd.read_csv("analisis/train_sj_clean2.csv")
data_iq = pd.read_csv("analisis/train_iq_clean2.csv")

# Características (sin la fecha y etiquetas)
features_sj = [col for col in data_sj.columns if col not in ["total_cases", "week_start_date"]]
features_iq = [col for col in data_iq.columns if col not in ["total_cases", "week_start_date"]]

# Función para evaluar los modelos
def evaluate_advanced_models(data, selected_features, imputer, scaler, transformation="log"):
    X = data[selected_features]
    y = data["total_cases"]

    # Separar en entrenamiento y prueba
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Imputación
    X_train = imputer.fit_transform(X_train)
    X_test = imputer.transform(X_test)

    # Aplicar transformación logarítmica
    if transformation == "log":
        X_train = np.log1p(np.abs(X_train))  # log(1 + x) para evitar problemas con ceros
        X_test = np.log1p(np.abs(X_test))

    # Escalado
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Modelos
    models = {
        "RandomForest": RandomForestRegressor(n_estimators=100, random_state=42),
        "XGBoost": XGBRegressor(n_estimators=100, random_state=42),
        "LightGBM": LGBMRegressor(n_estimators=100, random_state=42),
        "KNN": KNeighborsRegressor(n_neighbors=5),
        "NaiveBayes": GaussianNB()
    }

    results = {}
    for name, model in models.items():
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        results[name] = mean_absolute_error(y_test, y_pred)

    return results

# Imputador y escalador
imputer_sj = SimpleImputer(strategy="most_frequent")
imputer_iq = SimpleImputer(strategy="median")
scaler = StandardScaler()

# Evaluar para San Juan e Iquitos usando los datos LIMPIOS
results_sj = evaluate_advanced_models(data_sj, features_sj, imputer_sj, scaler, "log")
results_iq = evaluate_advanced_models(data_iq, features_iq, imputer_iq, scaler, "log")

# Crear DataFrame con los resultados
df_results = pd.DataFrame([results_sj, results_iq], index=["San Juan", "Iquitos"])

# Mostrar la tabla en el notebook
display(df_results)


c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000164 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3839
[LightGBM] [Info] Number of data points in the train set: 748, number of used features: 22
[LightGBM] [Info] Start training from score 34.330214
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


RandomForest    XGBoost   LightGBM        KNN  NaiveBayes
San Juan     15.322181  12.136500  16.724204  23.800000    32.62766
Iquitos       5.751442   5.510869   5.644914   7.344231     9.50000

XGBoost y LightGBM

In [28]:
import pandas as pd
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from sklearn.metrics import mean_absolute_error
import numpy as np

# Cargar los datos procesados
train_sj = pd.read_csv("analisis/train_sj_clean.csv")
train_iq = pd.read_csv("analisis/train_iq_clean.csv")

# Características (sin la fecha y etiquetas)
features = [col for col in train_sj.columns if col not in ["total_cases", "week_start_date"]]

# Preparar los datos
X_sj = train_sj[features]
y_sj = train_sj["total_cases"]
X_iq = train_iq[features]
y_iq = train_iq["total_cases"]

# Imputación y escalado
imputer_sj = SimpleImputer(strategy="most_frequent")
imputer_iq = SimpleImputer(strategy="median")
scaler = StandardScaler()

# Dividir en entrenamiento y prueba
X_train_sj, X_test_sj, y_train_sj, y_test_sj = train_test_split(X_sj, y_sj, test_size=0.2, random_state=42)
X_train_iq, X_test_iq, y_train_iq, y_test_iq = train_test_split(X_iq, y_iq, test_size=0.2, random_state=42)

# Preprocesar los datos
X_train_sj = imputer_sj.fit_transform(X_train_sj)
X_test_sj = imputer_sj.transform(X_test_sj)
X_train_iq = imputer_iq.fit_transform(X_train_iq)
X_test_iq = imputer_iq.transform(X_test_iq)

X_train_sj = scaler.fit_transform(X_train_sj)
X_test_sj = scaler.transform(X_test_sj)
X_train_iq = scaler.fit_transform(X_train_iq)
X_test_iq = scaler.transform(X_test_iq)

# Definir el espacio de búsqueda para XGBoost
xgb_param_grid = {
    'n_estimators': [100, 200],
    'learning_rate': [0.01, 0.1, 0.2],
    'max_depth': [3, 5, 7],
    'subsample': [0.8, 1.0]
}

# Definir el espacio de búsqueda para LightGBM
lgb_param_grid = {
    'n_estimators': [100, 200],
    'learning_rate': [0.01, 0.1, 0.2],
    'max_depth': [3, 5, 7],
    'num_leaves': [31, 50]
}

# Función para optimizar los modelos
def optimize_model(model, param_grid, X_train, y_train):
    grid_search = GridSearchCV(estimator=model, param_grid=param_grid, scoring='neg_mean_absolute_error', cv=5)
    grid_search.fit(X_train, y_train)
    return grid_search.best_params_, grid_search.best_score_

# Optimización de XGBoost y LightGBM para San Juan
best_params_xgb_sj, best_score_xgb_sj = optimize_model(XGBRegressor(random_state=42), xgb_param_grid, X_train_sj, y_train_sj)
best_params_lgb_sj, best_score_lgb_sj = optimize_model(LGBMRegressor(random_state=42), lgb_param_grid, X_train_sj, y_train_sj)

# Optimización de XGBoost y LightGBM para Iquitos
best_params_xgb_iq, best_score_xgb_iq = optimize_model(XGBRegressor(random_state=42), xgb_param_grid, X_train_iq, y_train_iq)
best_params_lgb_iq, best_score_lgb_iq = optimize_model(LGBMRegressor(random_state=42), lgb_param_grid, X_train_iq, y_train_iq)

# Función para evaluar los modelos
def evaluate_advanced_models(data, selected_features, imputer, scaler, transformation="log"):
    X = data[selected_features]
    y = data["total_cases"]

    # Separar en entrenamiento y prueba
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Imputación
    X_train = imputer.fit_transform(X_train)
    X_test = imputer.transform(X_test)

    # Aplicar transformación logarítmica
    if transformation == "log":
        X_train = np.log1p(np.abs(X_train))  # log(1 + x) para evitar problemas con ceros
        X_test = np.log1p(np.abs(X_test))

    # Escalado
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Modelos
    models = {
        "XGBoost": XGBRegressor(n_estimators=100, random_state=42),
        "LightGBM": LGBMRegressor(n_estimators=100, random_state=42)
    }

    results = {}
    for name, model in models.items():
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        results[name] = mean_absolute_error(y_test, y_pred)

    return results

# Evaluar los modelos optimizados para San Juan e Iquitos
sj_results = evaluate_advanced_models(train_sj, features, imputer_sj, scaler, "log")
iq_results = evaluate_advanced_models(train_iq, features, imputer_iq, scaler, "log")

# Imprimir los resultados
print("Resultados optimizados para San Juan:", sj_results)
print("Resultados optimizados para Iquitos:", iq_results)


c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000258 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3210
[LightGBM] [Info] Number of data points in the train set: 598, number of used features: 22
[LightGBM] [Info] Start training from score 33.170569
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000257 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3210
[LightGBM] [Info] Number of data points in the train set: 598, number of used features: 22
[LightGBM] [Info] Start training from score 33.170569
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure

...

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000349 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2437
[LightGBM] [Info] Number of data points in the train set: 416, number of used features: 22
[LightGBM] [Info] Start training from score 7.685096
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000347 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3839
[LightGBM] [Info] Number of data points in the train set: 748, number of used features: 22
[LightGBM] [Info] Start training from score 34.330214
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


Optimizar LightGBM

In [29]:
import pandas as pd
import lightgbm as lgb
import os
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler

# Crear carpeta para resultados
os.makedirs("resultado", exist_ok=True)

# Cargar datos preprocesados
train_sj = pd.read_csv("analisis/train_sj_clean.csv")
train_iq = pd.read_csv("analisis/train_iq_clean.csv")
test_features = pd.read_csv("dengue_features_test.csv")
submission_format = pd.read_csv("submission_format.csv")

# Definir características
features = [col for col in train_sj.columns if col not in ["total_cases", "week_start_date"]]

# Preparar conjuntos de entrenamiento
X_sj, y_sj = train_sj[features], train_sj["total_cases"]
X_iq, y_iq = train_iq[features], train_iq["total_cases"]

# Imputadores y escalador
imputer_sj = SimpleImputer(strategy="most_frequent")
imputer_iq = SimpleImputer(strategy="median")
scaler = StandardScaler()

# Aplicar preprocesamiento
X_sj = scaler.fit_transform(imputer_sj.fit_transform(X_sj))
X_iq = scaler.fit_transform(imputer_iq.fit_transform(X_iq))

# Separar test por ciudad
test_sj = test_features[test_features["city"] == "sj"][features]
test_iq = test_features[test_features["city"] == "iq"][features]

# Aplicar preprocesamiento a test
test_sj = scaler.transform(imputer_sj.transform(test_sj))
test_iq = scaler.transform(imputer_iq.transform(test_iq))

# Parámetros optimizados para LightGBM
params_sj = {
    "feature_fraction": 1.0, "lambda_l1": 0.0, "lambda_l2": 0.0, "learning_rate": 0.05,
    "max_depth": 7, "min_data_in_leaf": 20, "min_split_gain": 0.0,
    "n_estimators": 100, "num_leaves": 31
}
params_iq = {
    "feature_fraction": 1.0, "lambda_l1": 0.0, "lambda_l2": 0.2, "learning_rate": 0.05,
    "max_depth": 5, "min_data_in_leaf": 20, "min_split_gain": 0.2,
    "n_estimators": 100, "num_leaves": 31
}

# Entrenar modelos LightGBM
model_sj = lgb.LGBMRegressor(**params_sj)
model_sj.fit(X_sj, y_sj)

model_iq = lgb.LGBMRegressor(**params_iq)
model_iq.fit(X_iq, y_iq)

# Hacer predicciones
pred_sj = model_sj.predict(test_sj).round().astype(int)
pred_iq = model_iq.predict(test_iq).round().astype(int)

# Evitar valores negativos
pred_sj = pred_sj.clip(min=0)
pred_iq = pred_iq.clip(min=0)

# Crear archivo de submission
submission = submission_format.copy()
submission.loc[submission["city"] == "sj", "total_cases"] = pred_sj
submission.loc[submission["city"] == "iq", "total_cases"] = pred_iq

# Guardar submission en la carpeta "resultado"
submission_path = "resultado/submission_lightgbm.csv"
submission.to_csv(submission_path, index=False)

print(f"Archivo guardado en: {submission_path}")

[LightGBM] [Warning] min_data_in_leaf is set=20, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=20
[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
[LightGBM] [Warning] lambda_l1 is set=0.0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.0
[LightGBM] [Warning] lambda_l2 is set=0.0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.0
[LightGBM] [Warning] min_data_in_leaf is set=20, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=20
[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
[LightGBM] [Warning] lambda_l1 is set=0.0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.0
[LightGBM] [Warning] lambda_l2 is set=0.0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.0
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000176

c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\DevRoger\anaconda3\envs\tf-gpu\lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


Optimizar XGBoost

In [30]:
import pandas as pd
import xgboost as xgb
import os
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler

# Crear carpeta para resultados
os.makedirs("resultado", exist_ok=True)

# Cargar datos preprocesados
train_sj = pd.read_csv("analisis/train_sj_clean.csv")
train_iq = pd.read_csv("analisis/train_iq_clean.csv")
test_features = pd.read_csv("dengue_features_test.csv")
submission_format = pd.read_csv("submission_format.csv")

# Definir características
features = [col for col in train_sj.columns if col not in ["total_cases", "week_start_date"]]

# Preparar conjuntos de entrenamiento
X_sj, y_sj = train_sj[features], train_sj["total_cases"]
X_iq, y_iq = train_iq[features], train_iq["total_cases"]

# Imputadores y escalador
imputer_sj = SimpleImputer(strategy="most_frequent")
imputer_iq = SimpleImputer(strategy="median")
scaler = StandardScaler()

# Aplicar preprocesamiento
X_sj = scaler.fit_transform(imputer_sj.fit_transform(X_sj))
X_iq = scaler.fit_transform(imputer_iq.fit_transform(X_iq))

# Separar test por ciudad
test_sj = test_features[test_features["city"] == "sj"][features]
test_iq = test_features[test_features["city"] == "iq"][features]

# Aplicar preprocesamiento a test
test_sj = scaler.transform(imputer_sj.transform(test_sj))
test_iq = scaler.transform(imputer_iq.transform(test_iq))

# Parámetros óptimos para XGBoost
params_sj = {
    "objective": "reg:squarederror",
    "learning_rate": 0.05,
    "max_depth": 7,
    "n_estimators": 200,
    "subsample": 0.8,
    "colsample_bytree": 0.8
}
params_iq = {
    "objective": "reg:squarederror",
    "learning_rate": 0.05,
    "max_depth": 5,
    "n_estimators": 200,
    "subsample": 0.8,
    "colsample_bytree": 0.8
}

# Entrenar modelos XGBoost
model_sj = xgb.XGBRegressor(**params_sj)
model_sj.fit(X_sj, y_sj)

model_iq = xgb.XGBRegressor(**params_iq)
model_iq.fit(X_iq, y_iq)

# Hacer predicciones
pred_sj = model_sj.predict(test_sj).round().astype(int)
pred_iq = model_iq.predict(test_iq).round().astype(int)

# Evitar valores negativos
pred_sj = pred_sj.clip(min=0)
pred_iq = pred_iq.clip(min=0)

# Crear archivo de submission
submission = submission_format.copy()
submission.loc[submission["city"] == "sj", "total_cases"] = pred_sj
submission.loc[submission["city"] == "iq", "total_cases"] = pred_iq

# Guardar submission en la carpeta "resultado"
submission_path = "resultado/submission_xgboost.csv"
submission.to_csv(submission_path, index=False)

print(f"Archivo guardado en: {submission_path}")

Archivo guardado en: resultado/submission_xgboost.csv


Mejorar MAE XGBoost 1

In [31]:
import pandas as pd
import xgboost as xgb
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error

# Cargar datos preprocesados
train_sj = pd.read_csv("analisis/train_sj_clean.csv")
train_iq = pd.read_csv("analisis/train_iq_clean.csv")

# Definir características
features = [col for col in train_sj.columns if col not in ["total_cases", "week_start_date"]]

# Preparar conjuntos de entrenamiento
X_sj, y_sj = train_sj[features], train_sj["total_cases"]
X_iq, y_iq = train_iq[features], train_iq["total_cases"]

# Imputadores y escalador
imputer_sj = SimpleImputer(strategy="most_frequent")
imputer_iq = SimpleImputer(strategy="median")
scaler = StandardScaler()

# Aplicar preprocesamiento
X_sj = scaler.fit_transform(imputer_sj.fit_transform(X_sj))
X_iq = scaler.fit_transform(imputer_iq.fit_transform(X_iq))

# Dividir en entrenamiento (80%) y validación (20%)
X_train_sj, X_val_sj, y_train_sj, y_val_sj = train_test_split(X_sj, y_sj, test_size=0.2, random_state=42)
X_train_iq, X_val_iq, y_train_iq, y_val_iq = train_test_split(X_iq, y_iq, test_size=0.2, random_state=42)

# 🚀 **Nuevos hiperparámetros ajustados para XGBoost**
params_sj = {
    "objective": "reg:squarederror",
    "learning_rate": 0.03,  
    "max_depth": 6,  
    "n_estimators": 300,  
    "subsample": 0.8,
    "colsample_bytree": 0.8
}
params_iq = {
    "objective": "reg:squarederror",
    "learning_rate": 0.03,
    "max_depth": 5,  
    "n_estimators": 300,
    "subsample": 0.8,
    "colsample_bytree": 0.8
}

# Entrenar modelos XGBoost con los nuevos hiperparámetros
model_sj = xgb.XGBRegressor(**params_sj)
model_sj.fit(X_train_sj, y_train_sj)

model_iq = xgb.XGBRegressor(**params_iq)
model_iq.fit(X_train_iq, y_train_iq)

# Hacer predicciones en validación
pred_val_sj = model_sj.predict(X_val_sj).round().astype(int)
pred_val_iq = model_iq.predict(X_val_iq).round().astype(int)

# Evitar valores negativos
pred_val_sj = pred_val_sj.clip(min=0)
pred_val_iq = pred_val_iq.clip(min=0)

# Calcular MAE en validación
mae_sj = mean_absolute_error(y_val_sj, pred_val_sj)
mae_iq = mean_absolute_error(y_val_iq, pred_val_iq)

# MAE total promedio
mae_total = (mae_sj + mae_iq) / 2

print(f"MAE en validación para San Juan: {mae_sj}")
print(f"MAE en validación para Iquitos: {mae_iq}")
print(f"MAE total promedio: {mae_total}")

MAE en validación para San Juan: 13.148936170212766
MAE en validación para Iquitos: 5.076923076923077
MAE total promedio: 9.112929623567922
